In [1]:
# code to show/hide code cell

from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

In [2]:
import numpy as np
import urllib
import json
import re
from datetime import datetime as dt
from urllib.request import urlopen
import pandas as pd
from selenium import webdriver
import plotly.graph_objects as go
import plotly.figure_factory as ff
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support.select import Select
from selenium.webdriver.common.keys import Keys
from time import sleep
import sys
import requests
import random

## Selenium to scrape data ##
- Data source:丁香园实时疫情地图
- Select webelement by xpath
- Contents too messy to clean, try alternatives

notes: Scrapped ISO_3166-1 country code from wikipedia

In [3]:
# # using chrome as brower here, need change if use other browser
# path_to_chromedriver = 'C:\chromedriver\chromedriver.exe' # change path as needed
# chrome_options = webdriver.ChromeOptions() 
# driver = webdriver.Chrome(executable_path=path_to_chromedriver, options=chrome_options)

# # launch browser and go to target site
# driver.get("https://ncov.dxy.cn/ncovh5/view/pneumonia_peopleapp?from=timeline&isappinstalled=0")
# sleep(3)

# region_xpath = '//*[@id="root"]/div/div[5]/div[6]'
# region_elm = driver.find_element_by_xpath(region_xpath)
# contents = region_elm.get_attribute('innerHTML')
# driver.close()

In [4]:
path_to_chromedriver = 'C:\chromedriver\chromedriver.exe' # change path as needed
chrome_options = webdriver.ChromeOptions() 
driver = webdriver.Chrome(executable_path=path_to_chromedriver, options=chrome_options)

# go to website
driver.get("https://zh.wikipedia.org/zh-hk/ISO_3166-1%E4%B8%89%E4%BD%8D%E5%AD%97%E6%AF%8D%E4%BB%A3%E7%A0%81")
driver.maximize_window()
sleep(2)

# # log in my wikipedia account 
# driver.find_element_by_xpath('//*[@id="pt-login"]/a').click()
# sleep(2)

# user_path = '//*[@id="userloginForm"]/form/div/div[1]/div/input'
# pwd_path = '//*[@id="userloginForm"]/form/div/div[2]/div/input'
# login_path = '//*[@id="wpLoginAttempt"]'

#  # input username and password
# user_elem = driver.find_element_by_xpath(user_path)
# user_elem.send_keys('Bernard369')
# pwd_elem = driver.find_element_by_xpath(pwd_path)
# pwd_elem.send_keys('Crazy369')

# # press enter on "login" button
# login_elem = driver.find_element_by_xpath(login_path)
# login_elem.send_keys(Keys.RETURN)

In [5]:
# click dropdown menu
dropdown_path = '//*[@id="p-variants"]'
language_dropdown = driver.find_element_by_xpath(dropdown_path ).click()

# select language
language_cn_path = '//*[@id="ca-varlang-3"]'
language_cn = driver.find_element_by_xpath(language_cn_path ).click()
sleep(2)

region_xpath = '//*[@id="mw-content-text"]/div/table[1]'
region_elm = driver.find_element_by_xpath(region_xpath )
raw_contents = region_elm.text
driver.close()

In [6]:
# clean and reorganize scrapped ISO 3166-1 table

# remove some extra notes in table
contents = raw_contents.split('\n')
index = contents.index('TWN 中国台湾省[注 1]')
contents[index] = 'TWN 中国台湾省'
country, code = [], []

for i in range(len(contents)):
    temp1, temp2 = contents[i].split()
    country.append(temp2)
    code.append(temp1)

# store info in a pandas df
df_iso = pd.DataFrame({'国家': country, 'code': code})

## API to retrieve data ##
- API: https://lab.isaaclin.cn/nCoV/, open source
- Update data everytime you run the code
- Data in json format, data structure: world - China - Hubei cities


In [7]:
# use API to retrive data
response = requests.get("https://lab.isaaclin.cn/nCoV/api/area?latest=1&province=湖北省")
# verify everything went okay, and the result has been returned
assert response.status_code == 200
# extract city data in Hubei
city_data_json = response.json()['results'][0]['cities']

# empty lists to store record values
cityName, confirmedCount, curedCount, deadCount, locationId= [], [], [], [], []

for i in range(len(city_data_json)):
    cityName.append(city_data_json[i]['cityName'])
    confirmedCount.append(city_data_json[i]['confirmedCount'])
    curedCount.append(city_data_json[i]['curedCount'])
    deadCount.append(city_data_json[i]['deadCount'])
    locationId.append(city_data_json[i]['locationId'])
    
# create a table to store info
df_hubei = pd.DataFrame({'城市': cityName, '确诊':confirmedCount, '治愈':curedCount,
                         '死亡':deadCount, '地区代码':locationId})
# df_hubei

In [11]:
response = requests.get("https://lab.isaaclin.cn/nCoV/api/area?latest=1")
# verify everything went okay, and the result has been returned
assert response.status_code == 200
raw_data_json = response.json()['results']

country, provinceName, provinceShortName, confirmedCount, suspectedCount, \
curedCount, deadCount = [],[],[],[],[],[],[]

for i in range(len(raw_data_json)):
    country.append(raw_data_json[i]['countryName'])
    provinceName.append(raw_data_json[i]['provinceName'])
    provinceShortName.append(raw_data_json[i]['provinceShortName'])
    confirmedCount.append(raw_data_json[i]['confirmedCount'])
    suspectedCount.append(raw_data_json[i]['suspectedCount'])
    curedCount.append(raw_data_json[i]['curedCount'])
    deadCount.append(raw_data_json[i]['deadCount'])
        
# create a table to store info
df_raw = pd.DataFrame({'国家': country, '省': provinceName, '省简称':provinceShortName, 
                       '确诊':confirmedCount, '疑似': suspectedCount, '治愈':curedCount,'死亡':deadCount}) 

# clean and reorganize table
df_raw = df_raw.loc[df_raw['省']!= '待明确地区', :]
df_China = df_raw.loc[df_raw['国家'] == '中国', :]
df_World = df_raw.loc[df_raw['国家'] != '中国', ['国家','确诊','疑似', '治愈', '死亡']]
# df_China

In [21]:
df_World

国家     确诊    疑似     治愈    死亡 code               text
0          法国     12     0      4     1  FRA          法国\n12例确诊
1         比利时      1     0      1     0  BEL          比利时\n1例确诊
2         新加坡     75     0     19     0  SGP         新加坡\n75例确诊
3          日本     62     0     12     1  JPN          日本\n62例确诊
4          埃及      1     0      0     0  EGY           埃及\n1例确诊
5          印度      3     0      3     0  IND           印度\n3例确诊
6        马来西亚     22     0      7     0  MYS        马来西亚\n22例确诊
7          英国      9     0      8     0  GBR           英国\n9例确诊
8     钻石公主号邮轮    355     0      0     0  NaN    钻石公主号邮轮\n355例确诊
9        澳大利亚     15     0     10     0  AUS        澳大利亚\n15例确诊
10         韩国     30     0      9     0  KOR          韩国\n30例确诊
11         泰国     34     0     14     0  THA          泰国\n34例确诊
12        阿联酋      9     0      4     0  ARE          阿联酋\n9例确诊
13        加拿大      8     0      2     0  CAN          加拿大\n8例确诊
14         美国     15     0      3     0  USA          美国\n15例确诊
15         越南     16     0      7     0  VNM          越南\n16例确诊
16         德国     16     0      1     0  DEU          德国\n16例确诊
17        俄罗斯      2     0      2     0  RUS          俄罗斯\n2例确诊
18        柬埔寨      1     0      1     0  KHM          柬埔寨\n1例确诊
19        意大利      3     0      0     0  ITA          意大利\n3例确诊
20        西班牙      2     0      0     0  ESP          西班牙\n2例确诊
21       斯里兰卡      1     0      0     0  LKA         斯里兰卡\n1例确诊
22         芬兰      1     0      1     0  FIN           芬兰\n1例确诊
23        尼泊尔      1     0      0     0  NPL          尼泊尔\n1例确诊
24        菲律宾      3     0      1     1  PHL          菲律宾\n3例确诊
25         瑞典      1     0      0     0  SWE           瑞典\n1例确诊
26  “钻石公主”号邮轮    355     0      0     0  NaN  “钻石公主”号邮轮\n355例确诊
27  「钻石公主」号邮轮    355     0      0     0  NaN  「钻石公主」号邮轮\n355例确诊
28         邮轮    355     0      0     0  NaN         邮轮\n355例确诊
29         中国  70638  7264  10978  1772  CHN       中国\n70638例确诊
30         中国  70638  7264  10978  1772  TWN       中国\n70638例确诊

In [12]:
response = requests.get("https://lab.isaaclin.cn/nCoV/api/overall")
# verify everything went okay, and the result has been returned
assert response.status_code == 200
China_summary_json = response.json()['results'][0] 
China_counts = {'国家':'中国',  '确诊': China_summary_json['confirmedCount'], 
                              '疑似': China_summary_json['suspectedCount'], 
                              '治愈': China_summary_json['curedCount'],
                              '死亡': China_summary_json['deadCount']}
# append China data to World data table
df_World = df_World.append(China_counts, ignore_index=True)

# merge iso code to df
df_World = df_World.merge(df_iso, how = 'left', on = '国家')

# correct TW
TW_correct = {'国家':'中国',  '确诊': China_summary_json['confirmedCount'], 
                              '疑似': China_summary_json['suspectedCount'], 
                              '治愈': China_summary_json['curedCount'],
                              '死亡': China_summary_json['deadCount'], 
              'code': 'TWN'}

# append China data to World data table
df_World = df_World.append(TW_correct, ignore_index=True)
time_stamp = dt.fromtimestamp(China_summary_json['updateTime'] / 1000)
print('数据更新于%s'%(time_stamp ))

数据更新于2020-02-16 23:15:41.559000


In [13]:
# # time series summary stats
# response = requests.get("https://lab.isaaclin.cn/nCoV/api/overall?latest=0")
# # verify everything went okay, and the result has been returned
# assert response.status_code == 200
# raw_series_json = response.json()['results']

# confirmedCount, suspectedCount, curedCount, deadCount, seriousCount, \
# suspectedIncr, confirmedIncr, curedIncr, deadIncr, seriousIncr, updateTime \
# = [], [], [], [], [], [], [], [], [], [], []

# for i in range(len(raw_series_json)):
#     confirmedCount.append(raw_series_json[i]['confirmedCount'])
#     suspectedCount.append(raw_series_json[i]['suspectedCount'])
#     curedCount.append(raw_series_json[i]['curedCount'])
#     deadCount.append(raw_series_json[i]['deadCount'])
#     updateTime.append(raw_series_json[i]['updateTime'])
    
#     if 'seriousCount' in raw_series_json[i].keys():
#         seriousCount.append(raw_series_json[i]['seriousCount'])
#     else:
#         seriousCount.append( np.nan )
    
#     if 'suspectedIncr' in raw_series_json[i].keys():
#         suspectedIncr.append(raw_series_json[i]['suspectedIncr'])
#         confirmedIncr.append(raw_series_json[i]['confirmedIncr'])
#         curedIncr.append(raw_series_json[i]['curedIncr'])
#         deadIncr.append(raw_series_json[i]['deadIncr'])
#         seriousIncr.append(raw_series_json[i]['seriousIncr'])
        
#     else:
#         suspectedIncr.append( np.nan )
#         confirmedIncr.append( np.nan )
#         curedIncr.append( np.nan )
#         deadIncr.append( np.nan )
#         seriousIncr.append( np.nan )
  
# df_time = pd.DataFrame({'确诊':confirmedCount, '疑似': suspectedCount, '治愈':curedCount,
#                         '死亡':deadCount, '重症':seriousCount, '疑似增数':suspectedIncr,
#                         '确诊增数':confirmedIncr, '治愈增数':curedIncr, '死亡增数':deadIncr,
#                         '重症增数':seriousIncr, '更新时间值':updateTime}) 
# # df_time

## Data Visualization ## 

In [14]:
# # world heatmap on confirmed cases

# fig = go.Figure(data=go.Choropleth(
#     locations = df_World['code'],
#     z = np.log10(df_World['确诊']),
#     text = df_World['国家'],
#     colorscale = 'Reds',
#     #reversescale=True,
#     #autocolorscale= True,
#     marker_line_color='darkgray',
#     marker_line_width=0.5,
#     colorbar_title = '确诊病例'
# ))

# fig.update_layout(
#     title_text='2019 nCov 全球确诊热图',
#     geo=dict(
#         showframe=False,
#         showcoastlines=False
#     )
# )

# fig.show()

In [15]:
# prepare token for Mapbox
token = 'pk.eyJ1IjoiY2h1emhpY29uZyIsImEiOiJjazZoMG5tajIwNmh4M21ueGN0eXdtMmx6In0.kQscrYmKzfyLhN-YgENO0Q'

# load map file
with urlopen('https://raw.githubusercontent.com/johan/world.geo.json/master/countries.geo.json') as response:
    world_geo = json.load(response)
    
# set up hovertext
text = [ df_World['国家'][i] + '\n' +  str(df_World['确诊'][i]) + '例确诊'  for i in range(len(df_World))]
df_World['text'] = text

# World heatmap by province on confirmed cases

fig = go.Figure(go.Choroplethmapbox(geojson = world_geo, locations = df_World['code'],
                                    z = np.log10(df_World['确诊']), hovertext = df_World['text'],
                                    hoverinfo = 'text', colorscale = 'YlOrRd',
                                    marker_line_width = 0.5, marker_line_color = 'rgb(169, 164, 159)',
                                    colorbar=dict(
                                       title="确诊病例数",
                                       titleside="top",
                                       tickmode="array",
                                       tickvals=np.arange(0, 5, 1),
                                       ticktext=["1", "10", "100", "1k", '10k', '100k'],
                                       ticks="outside"
                                    )))

fig.update_layout(mapbox = {'accesstoken': token, 'center':{'lon' : 109.469607, 'lat': 37.826077},'zoom': 1},
                  margin={"r":0,"t":35,"l":0,"b":0}, title = '疫情地图-World',
                  annotations = [dict(
                      x=0.55,
                      y=0.03,
                      xref='paper',
                      yref='paper',
                      text='数据更新于 ' + str(time_stamp) ,
                      showarrow = False
                 )])
fig.show()

In [16]:
# load map file
with urlopen('https://raw.githubusercontent.com/johan/world.geo.json/6a1119de83dad01e07524e2ab97c2a1f54b9ef53/countries/CHN.geo.json') as response:
    china_geo = json.load(response)

# extract province ids (used for locations) from json file
ids, provinces = [], []

for i in range(len(china_geo['features'])):
    ids.append( china_geo['features'][i]['id'] )
    provinces.append( china_geo['features'][i]['properties']['name'] )
    
df_province_code = pd.DataFrame({'省简称': provinces, 'code': ids})
df_China = df_China.merge(df_province_code, how = 'left', on = '省简称')

# set up hovertext
text = [ df_China['省简称'][i] + '\n' +  str(df_China['确诊'][i]) + '例确诊'  for i in range(len(df_China))]
df_China['text'] = text

In [17]:
# China heatmap by province on confirmed cases
fig = go.Figure(go.Choroplethmapbox(geojson = china_geo, locations = df_China['code'],
                                    z = np.log10(df_China['确诊']), hovertext = df_China['text'],
                                    hoverinfo = 'text', colorscale = 'YlOrRd',
                                    marker_line_width = 0.5, marker_line_color = 'rgb(169, 164, 159)',
                                    colorbar=dict(
                                       title="确诊病例数",
                                       titleside="top",
                                       tickmode="array",
                                       tickvals=np.arange(0, 5, 1),
                                       ticktext=["1", "10", "100", "1k", '10k', '100k'],
                                       ticks="outside"
                                    )))

fig.update_layout(mapbox = {'accesstoken': token, 'center':{'lon' : 109.469607, 'lat': 37.826077},'zoom': 2.6},
                  margin={"r":0,"t":35,"l":0,"b":0}, title = '疫情地图-China',
                  annotations = [dict(
                      x=0.85,
                      y=0.03,
                      xref='paper',
                      yref='paper',
                      text='数据更新于 ' + str(time_stamp) ,
                      showarrow = False
                 )])
fig.show()

In [18]:
# load map file
with urlopen('https://raw.githubusercontent.com/longwosion/geojson-map-china/master/geometryProvince/42.json') as response:
    hubei_geo = json.load(response)
    
# reorganize ids
hubei_features = []
for i in range(len(hubei_geo['features'])):
    temp_feature = hubei_geo['features'][i]
    temp_feature['id'] = temp_feature['properties']['id']
    hubei_features.append(temp_feature)

hubei_geo['features'] = hubei_features
# extract province ids (used for locations) from json file
ids, cities = [], []

for i in range(len(hubei_geo['features'])):
    ids.append( hubei_geo['features'][i]['id'] )
    cities.append( hubei_geo['features'][i]['properties']['name'] )
    
df_city_code = pd.DataFrame({'城市全称': cities, 'code': ids})
df_city_code['城市'] = ['恩施州', '十堰', '宜昌', '襄阳', '黄冈', '荆州', '荆门', '咸宁', '随州',
                       '孝感', '武汉', '黄石', '神农架林区', '天门', '仙桃', '潜江', '鄂州']
df_hubei = df_hubei.merge(df_city_code, how = 'left', on = '城市')

# set up hovertext
text = [ df_hubei['城市'][i] + '\n' +  str(df_hubei['确诊'][i]) + '例确诊'  for i in range(len(df_hubei))]
df_hubei['text'] = text

In [19]:
# Hubei heatmap by province on confirmed cases
fig = go.Figure(go.Choroplethmapbox(geojson = hubei_geo, locations = df_hubei['code'],
                                    z = np.log10(df_hubei['确诊']), hovertext = df_hubei['text'],
                                    hoverinfo = 'text', colorscale = 'YlOrRd',
                                    marker_line_width = 0.5, marker_line_color = 'rgb(169, 164, 159)',
                                    colorbar=dict(
                                       title="确诊病例数",
                                       titleside="top",
                                       tickmode="array",
                                       tickvals=np.arange(0, 5, 1),
                                       ticktext=["1", "10", "1k", '10k', '100k', '1M'],
                                       ticks="outside"
                                    )))

fig.update_layout(mapbox = {'accesstoken': token, 'center':{'lon' : 112.1994, 'lat': 31.0354},'zoom': 6},
                  margin={"r":0,"t":35,"l":0,"b":0}, title = '疫情地图-Hubei',
                  annotations = [dict(
                      x=0.55,
                      y=0.03,
                      xref='paper',
                      yref='paper',
                      text='数据更新于 ' + str(time_stamp),
                      showarrow = False
                 )])
fig.show()